In [34]:
import fiftyone.zoo as foz

In [44]:
dataset = foz.load_zoo_dataset(
    "coco-2017",
    splits=["train", "validation", "test"],
    label_types=[ "segmentations"],
    classes=['person','bicycle','car','motorcycle'],
    
)

 100% |██████|    1.9Gb/1.9Gb [16.7s elapsed, 0s remaining, 139.7Mb/s]      
Extracting annotations to '/home/savkin/fiftyone/coco-2017/raw/instances_train2017.json'
 100% |██████████████| 68777/68777 [41.1m elapsed, 0s remaining, 19.5 images/s]      
Writing annotations for 68777 downloaded samples to '/home/savkin/fiftyone/coco-2017/train/labels.json'
Found annotations at '/home/savkin/fiftyone/coco-2017/raw/instances_val2017.json'
 100% |████████████████| 2910/2910 [1.8m elapsed, 0s remaining, 25.3 images/s]      
Writing annotations for 2910 downloaded samples to '/home/savkin/fiftyone/coco-2017/validation/labels.json'
Test split is unlabeled; ignoring classes requirement
 100% |██████|    8.7Mb/8.7Mb [611.5ms elapsed, 0s remaining, 14.3Mb/s]     
Extracting test info to '/home/savkin/fiftyone/coco-2017/raw/image_info_test2017.json'
 100% |█████|   49.5Gb/49.5Gb [9.6m elapsed, 0s remaining, 94.7Mb/s]       
Extracting images to '/home/savkin/fiftyone/coco-2017/test/data'
Writing an

In [35]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import skimage.io as io
import cv2
import os
import sys
from pycocotools.coco import COCO
import functools
import tensorflow as tf
import tensorflow_datasets as tfds
from tensorflow.keras.layers import Conv2D
from pycocotools.coco import COCO
from tensorflow.keras.callbacks import TensorBoard, ModelCheckpoint
from tensorflow.keras.models import Model, load_model
from tensorflow.keras.layers import *

In [9]:

def down_block(
    input_tensor,
    no_filters,
    kernel_size=(3, 3),
    strides=(1, 1),
    padding="same",
    kernel_initializer="he_normal",
    max_pool_window=(2, 2),
    max_pool_stride=(2, 2)
):
    conv = Conv2D(
        filters=no_filters,
        kernel_size=kernel_size,
        strides=strides,
        input_shape = (32,32,3),
        activation=None,
        padding=padding,
        kernel_initializer=kernel_initializer
    )(input_tensor)

    conv = BatchNormalization(scale=True)(conv)

    conv = Activation("relu")(conv)

    conv = Conv2D(
        filters=no_filters,
        kernel_size=kernel_size,
        strides=strides,
        activation=None,
        padding=padding,
        kernel_initializer=kernel_initializer
    )(conv)

    conv = BatchNormalization(scale=True)(conv)

    # conv for skip connection
    conv = Activation("relu")(conv)

    pool = MaxPooling2D(pool_size=max_pool_window, strides=max_pool_stride)(conv)

    return conv, pool
def bottle_neck(
    input_tensor,
    no_filters,
    kernel_size=(3, 3),
    strides=(1, 1),
    padding="same",
    kernel_initializer="he_normal"
):
    conv = Conv2D(
        filters=no_filters,
        kernel_size=kernel_size,
        strides=strides,
        activation=None,
        padding=padding,
        kernel_initializer=kernel_initializer
    )(input_tensor)

    conv = BatchNormalization(scale=True)(conv)

    conv = Activation("relu")(conv)

    conv = Conv2D(
        filters=no_filters,
        kernel_size=kernel_size,
        strides=strides,
        activation=None,
        padding=padding,
        kernel_initializer=kernel_initializer
    )(conv)

    conv = BatchNormalization(scale=True)(conv)

    conv = Activation("relu")(conv)

    return conv
def up_block(    
    input_tensor,
    no_filters,
    skip_connection, 
    kernel_size=(3, 3),
    strides=(1, 1),
    upsampling_factor = (2,2),
    max_pool_window = (2,2),
    padding="same",
    kernel_initializer="he_normal"):
    
    
    conv = Conv2D(
        filters = no_filters,
        kernel_size= max_pool_window,
        strides = strides,
        activation = None,
        padding = padding,
        kernel_initializer=kernel_initializer
    )(UpSampling2D(size = upsampling_factor)(input_tensor))
    
    conv = BatchNormalization(scale=True)(conv)

    conv = Activation("relu")(conv) 
    
    
    conv = concatenate( [skip_connection , conv]  , axis = -1)
    
    
    conv = Conv2D(
        filters=no_filters,
        kernel_size=kernel_size,
        strides=strides,
        activation=None,
        padding=padding,
        kernel_initializer=kernel_initializer
    )(conv)

    conv = BatchNormalization(scale=True)(conv)

    conv = Activation("relu")(conv)

    conv = Conv2D(
        filters=no_filters,
        kernel_size=kernel_size,
        strides=strides,
        activation=None,
        padding=padding,
        kernel_initializer=kernel_initializer
    )(conv)

    conv = BatchNormalization(scale=True)(conv)

    conv = Activation("relu")(conv)
    
    return conv
def output_block(input_tensor,
    padding="same",
    kernel_initializer="he_normal"
):
    
    conv = Conv2D(
        filters=2,
        kernel_size=(3,3),
        strides=(1,1),
        activation="relu",
        padding=padding,
        kernel_initializer=kernel_initializer
    )(input_tensor)
    
    
    conv = Conv2D(
        filters=1,
        kernel_size=(1,1),
        strides=(1,1),
        activation="sigmoid",
        padding=padding,
        kernel_initializer=kernel_initializer
    )(conv)
    
    
    return conv
    
def UNet(input_shape = (128,128,3)):
    
    filter_size = [64,128,256,512,1024]
    
    inputs = Input(shape = input_shape)
    
    d1 , p1 = down_block(input_tensor= inputs,
                         no_filters=filter_size[0],
                         kernel_size = (3,3),
                         strides=(1,1),
                         padding="same",
                         kernel_initializer="he_normal",
                         max_pool_window=(2,2),
                         max_pool_stride=(2,2))
    
    
    d2 , p2 = down_block(input_tensor= p1,
                         no_filters=filter_size[1],
                         kernel_size = (3,3),
                         strides=(1,1),
                         padding="same",
                         kernel_initializer="he_normal",
                         max_pool_window=(2,2),
                         max_pool_stride=(2,2))
    
    
    
    d3 , p3 = down_block(input_tensor= p2,
                         no_filters=filter_size[2],
                         kernel_size = (3,3),
                         strides=(1,1),
                         padding="same",
                         kernel_initializer="he_normal",
                         max_pool_window=(2,2),
                         max_pool_stride=(2,2))
    
    
    
    d4 , p4 = down_block(input_tensor= p3,
                         no_filters=filter_size[3],
                         kernel_size = (3,3),
                         strides=(1,1),
                         padding="same",
                         kernel_initializer="he_normal",
                         max_pool_window=(2,2),
                         max_pool_stride=(2,2))
    
    
    b = bottle_neck(input_tensor= p4,
                         no_filters=filter_size[4],
                         kernel_size = (3,3),
                         strides=(1,1),
                         padding="same",
                         kernel_initializer="he_normal")
    
    
    
    u4 = up_block(input_tensor = b,
                  no_filters = filter_size[3],
                  skip_connection = d4,
                  kernel_size=(3, 3),
                  strides=(1, 1),
                  upsampling_factor = (2,2),
                  max_pool_window = (2,2),
                  padding="same",
                  kernel_initializer="he_normal")
    
    u3 = up_block(input_tensor = u4,
                  no_filters = filter_size[2],
                  skip_connection = d3,
                  kernel_size=(3, 3),
                  strides=(1, 1),
                  upsampling_factor = (2,2),
                  max_pool_window = (2,2),
                  padding="same",
                  kernel_initializer="he_normal")
    
    
    u2 = up_block(input_tensor = u3,
                  no_filters = filter_size[1],
                  skip_connection = d2,
                  kernel_size=(3, 3),
                  strides=(1, 1),
                  upsampling_factor = (2,2),
                  max_pool_window = (2,2),
                  padding="same",
                  kernel_initializer="he_normal")
    
    
    u1 = up_block(input_tensor = u2,
                  no_filters = filter_size[0],
                  skip_connection = d1,
                  kernel_size=(3, 3),
                  strides=(1, 1),
                  upsampling_factor = (2,2),
                  max_pool_window = (2,2),
                  padding="same",
                  kernel_initializer="he_normal")
    
    
    
    output = output_block(input_tensor=u1 , 
                         padding = "same",
                         kernel_initializer= "he_normal")
    
    model = tf.keras.models.Model(inputs = inputs , outputs = output)
    
    
    return model

In [29]:
class CustomDataLoader(tf.keras.utils.Sequence):

    def __init__(self, annFile, image_dir, mask_dir, categories, batch_size):
        self.annFile = annFile
        self.coco = COCO(annFile)
        catIds = self.coco.getCatIds(catNms=categories)
        # Get the corresponding image ids and images using loadImgs
        imgIds = self.coco.getImgIds(catIds=catIds)
        self.images = self.coco.loadImgs(imgIds)
        self.images_count = len(self.images)
        self.image_dir  = image_dir
        self.batch_size = batch_size
        self.mask_dir = mask_dir
        self.ids = os.listdir(self.image_dir)
        self.image_size = 512


    def __load__(self, id_name):
        
        image_path = os.path.join(self.image_dir , id_name)
        mask_path = os.path.join(self.mask_dir , id_name)
        image = cv2.imread(image_path , 1) # 1 specifies RGB format
        image = cv2.resize(image , (self.image_size , self.image_size)) # resizing before inserting to the network
        
        mask = cv2.imread(mask_path , -1)
        mask = cv2.resize(mask , (self.image_size , self.image_size))
        mask = mask.reshape((self.image_size , self.image_size , 1))
        
       
        image = image / 255.0
        mask = mask / 255.0
        
        return image , mask

    def  __getitem__(self , index):
       
        if (index + 1)*self.batch_size > len(self.ids):
            self.batch_size = len(self.ids) - index * self.batch_size
            
        file_batch = self.ids[index * self.batch_size : (index + 1) * self.batch_size]
        
        images = []
        masks = []
        
        for id_name in file_batch : 
        
            _img , _mask = self.__load__(id_name)
            images.append(_img)
            masks.append(_mask)
        
        
        images = np.array(images)
        masks = np.array(masks)
        
        
        return images , masks
       
    def __len__(self):
         return int(np.ceil(len(self.ids) / float(self.batch_size)))

    def on_epoch_end(self):
        pass      
    

In [104]:
!mkdir mask_val_2017

In [105]:
!mkdir mask_train_2017

In [19]:
!pwd

/home/savkin/unet_myself


In [1]:
from pycocotools import coco, cocoeval, _mask
from pycocotools import mask as maskUtils 
import array
import numpy as np
import skimage.io as io
import matplotlib.pyplot as plt
import pylab
import os

In [2]:
CATEGORY_NAMES=['person','bicycle','car','motorcycle']

ANNOTATION_FILE_VAL = '../fiftyone/coco-2017/validation/labels.json'
ANNOTATION_FILE_TRAIN = '../fiftyone/coco-2017/train/labels.json'


coco_train = coco.COCO(ANNOTATION_FILE_TRAIN)
catIds_train = coco_train.getCatIds(catNms=CATEGORY_NAMES);
imgIds_train = coco_train.getImgIds(catIds=catIds_train);
imgDict_train = coco_train.loadImgs(imgIds_train)
len(imgIds_train) , len(catIds_train)





coco_val = coco.COCO(ANNOTATION_FILE_VAL)
catIds_val = coco_val.getCatIds(catNms=CATEGORY_NAMES);
imgIds_val = coco_val.getImgIds(catIds=catIds_val);
imgDict_val = coco_val.loadImgs(imgIds_val)
len(imgIds_val) , len(catIds_val)


loading annotations into memory...
Done (t=8.05s)
creating index...
index created!
loading annotations into memory...
Done (t=0.26s)
creating index...
index created!


(10, 4)

In [3]:
imgIds_train

[562176,
 344067,
 203269,
 340998,
 226825,
 262670,
 465424,
 57361,
 12818,
 78355,
 294933,
 298008,
 242202,
 267802,
 575008,
 283170,
 210980,
 301605,
 53803,
 564781,
 506927,
 551472,
 246833,
 14388,
 225848,
 455228,
 372804,
 123975,
 573513,
 9801,
 405580,
 212558,
 135250,
 321107,
 216150,
 357976,
 6233,
 426585,
 15451,
 322143,
 274528,
 460897,
 492131,
 173161,
 90218,
 95850,
 467564,
 255604,
 385145,
 504958,
 253054,
 490112,
 507520,
 490629,
 155270,
 448648,
 128137,
 576650,
 538249,
 241291,
 568972,
 126606,
 578705,
 12946,
 469139,
 503957,
 108701,
 155806,
 127134,
 415904,
 316063,
 505501,
 445603,
 219300,
 45222,
 319655,
 392363,
 343213,
 470190,
 70321,
 526514,
 534195,
 528566,
 28855,
 272569,
 336576,
 12993,
 43202,
 417987,
 518850,
 513729,
 573125,
 402632,
 482505,
 536265,
 199883,
 32458,
 21711,
 22741,
 442582,
 327895,
 575702,
 422105,
 251098,
 32471,
 243418,
 213215,
 551647,
 391397,
 99046,
 146151,
 66789,
 493812,
 392949

In [4]:
from PIL import Image

In [5]:
for ID in imgIds_train: 
    sampleImgIds = coco_train.getImgIds(imgIds = [ID])
    print("F ", sampleImgIds)
    sampleImgDict = coco_train.loadImgs(sampleImgIds[np.random.randint(0,len(sampleImgIds))])[0]
    print("S", sampleImgDict)

F  [562176]
S {'license': 3, 'file_name': '000000562176.jpg', 'coco_url': 'http://images.cocodataset.org/train2017/000000562176.jpg', 'height': 341, 'width': 640, 'date_captured': '2013-11-15 15:36:42', 'flickr_url': 'http://farm8.staticflickr.com/7321/9170802006_2734814bd7_z.jpg', 'id': 562176}
F  [344067]
S {'license': 3, 'file_name': '000000344067.jpg', 'coco_url': 'http://images.cocodataset.org/train2017/000000344067.jpg', 'height': 421, 'width': 640, 'date_captured': '2013-11-15 01:24:25', 'flickr_url': 'http://farm8.staticflickr.com/7353/9715487608_f3f5e9b4dd_z.jpg', 'id': 344067}
F  [203269]
S {'license': 2, 'file_name': '000000203269.jpg', 'coco_url': 'http://images.cocodataset.org/train2017/000000203269.jpg', 'height': 375, 'width': 500, 'date_captured': '2013-11-17 06:13:37', 'flickr_url': 'http://farm4.staticflickr.com/3202/2345517887_36ef2e7551_z.jpg', 'id': 203269}
F  [340998]
S {'license': 2, 'file_name': '000000340998.jpg', 'coco_url': 'http://images.cocodataset.org/trai

In [106]:
count = 0 

for ID in imgIds_train:

  
  
  sampleImgIds = coco_train.getImgIds(imgIds = [ID])
  sampleImgDict = coco_train.loadImgs(sampleImgIds[np.random.randint(0,len(sampleImgIds))])[0]

  annIds = coco_train.getAnnIds(imgIds=sampleImgDict['id'], catIds=catIds_train, iscrowd=0)
  anns = coco_train.loadAnns(annIds)
  file_path = "mask_train_2017/COCO_train2017_{}".format(sampleImgDict['file_name'])  

  mask = coco_train.annToMask(anns[0])
  for i in range(len(anns)):
      mask = mask | coco_train.annToMask(anns[i])
  
  mask = Image.fromarray(mask * 255 , mode = "L")
  mask.save(file_path)
  count = count + 1
  print(count, file_path)

1 mask_train_2017/COCO_train2017_000000562176.jpg
2 mask_train_2017/COCO_train2017_000000344067.jpg
3 mask_train_2017/COCO_train2017_000000203269.jpg
4 mask_train_2017/COCO_train2017_000000340998.jpg
5 mask_train_2017/COCO_train2017_000000226825.jpg
6 mask_train_2017/COCO_train2017_000000262670.jpg
7 mask_train_2017/COCO_train2017_000000465424.jpg
8 mask_train_2017/COCO_train2017_000000057361.jpg
9 mask_train_2017/COCO_train2017_000000012818.jpg
10 mask_train_2017/COCO_train2017_000000078355.jpg
11 mask_train_2017/COCO_train2017_000000294933.jpg
12 mask_train_2017/COCO_train2017_000000298008.jpg
13 mask_train_2017/COCO_train2017_000000242202.jpg
14 mask_train_2017/COCO_train2017_000000267802.jpg
15 mask_train_2017/COCO_train2017_000000575008.jpg
16 mask_train_2017/COCO_train2017_000000283170.jpg
17 mask_train_2017/COCO_train2017_000000210980.jpg
18 mask_train_2017/COCO_train2017_000000301605.jpg
19 mask_train_2017/COCO_train2017_000000053803.jpg
20 mask_train_2017/COCO_train2017_000000

186 mask_train_2017/COCO_train2017_000000226705.jpg
187 mask_train_2017/COCO_train2017_000000578962.jpg
188 mask_train_2017/COCO_train2017_000000232339.jpg
189 mask_train_2017/COCO_train2017_000000458650.jpg
190 mask_train_2017/COCO_train2017_000000317851.jpg
191 mask_train_2017/COCO_train2017_000000305573.jpg
192 mask_train_2017/COCO_train2017_000000272807.jpg
193 mask_train_2017/COCO_train2017_000000250794.jpg
194 mask_train_2017/COCO_train2017_000000423341.jpg
195 mask_train_2017/COCO_train2017_000000013230.jpg
196 mask_train_2017/COCO_train2017_000000392111.jpg
197 mask_train_2017/COCO_train2017_000000142259.jpg
198 mask_train_2017/COCO_train2017_000000560563.jpg
199 mask_train_2017/COCO_train2017_000000241076.jpg
200 mask_train_2017/COCO_train2017_000000468405.jpg
201 mask_train_2017/COCO_train2017_000000229301.jpg
202 mask_train_2017/COCO_train2017_000000204217.jpg
203 mask_train_2017/COCO_train2017_000000117178.jpg
204 mask_train_2017/COCO_train2017_000000255418.jpg
205 mask_tra

In [41]:
count = 0 
for ID in imgIds_val:

  # file_path = "mask_val_2017/COCO_val2017_{0:012d}.jpg".format(ID)
  
  sampleImgIds = coco_val.getImgIds(imgIds = [ID])
  sampleImgDict = coco_val.loadImgs(sampleImgIds[np.random.randint(0,len(sampleImgIds))])[0]

  annIds = coco_val.getAnnIds(imgIds=sampleImgDict['id'], catIds=catIds_val, iscrowd=0)
  anns = coco_val.loadAnns(annIds)

  file_path = "mask_val_2017/COCO_val2017_{}".format(sampleImgDict['file_name'])    
  mask = coco_val.annToMask(anns[0])
  for i in range(len(anns)):
      mask = mask | coco_val.annToMask(anns[i])
  
  mask = Image.fromarray(mask * 255 , mode = "L")
  mask.save(file_path)
  
  count = count + 1
  print(count)

1
2
3
4
5
6
7
8
9
10


In [30]:
image_size = 128 
epochs = 10
batch_size = 8
input_shape = (512, 512, 3)
model = UNet(input_shape = (512,512,3))
model.compile(optimizer = tf.keras.optimizers.Adam(lr = 1e-4),run_eagerly=True, loss = 'binary_crossentropy', metrics = ['accuracy'])
base_lr = 0.02
train_ds = CustomDataLoader(annFile='../fiftyone/coco-2017/train/labels.json', image_dir='../fiftyone/coco-2017/train/data/', mask_dir='mask_train_2017', categories=['person'], batch_size=8)
val_ds = CustomDataLoader(annFile='../fiftyone/coco-2017/validation/labels.json', image_dir='../fiftyone/coco-2017/validation/data/', mask_dir='mask_val_2017', categories=['person'], batch_size=8)
   

loading annotations into memory...
Done (t=0.03s)
creating index...
index created!
loading annotations into memory...
Done (t=0.02s)
creating index...
index created!


In [31]:
train_steps =  len(os.listdir( "../fiftyone/coco-2017/train/data/"))/ 8
model.fit_generator(train_ds , validation_data = val_ds , steps_per_epoch = train_steps , epochs=epochs)


/tmp/ipykernel_3577716/2848843947.py:2: UserWarning: `Model.fit_generator` is deprecated and will be removed in a future version. Please use `Model.fit`, which supports generators.
  model.fit_generator(train_ds , validation_data = val_ds , steps_per_epoch = train_steps , epochs=epochs)
[ WARN:0@727.575] global /io/opencv/modules/imgcodecs/src/loadsave.cpp (239) findDecoder imread_('mask_train_2017/000000124739.jpg'): can't open/read file: check file path/integrity


error: OpenCV(4.5.5) /io/opencv/modules/imgproc/src/resize.cpp:4052: error: (-215:Assertion failed) !ssize.empty() in function 'resize'


In [ ]:
!cat ../fiftyone/coco-2017/validation/labels.json 

In [52]:
from pycocotools import coco, cocoeval, _mask
from pycocotools import mask as maskUtils 
CATEGORY_NAMES=['person','bicycle','car','motorcycle']

ANNOTATION_FILE_VAL = '../fiftyone/coco-2017/validation/labels.json'
ANNOTATION_FILE_TRAIN = '../fiftyone/coco-2017/train/labels.json'


coco_train = coco.COCO(ANNOTATION_FILE_TRAIN)
catIds_train = coco_train.getCatIds(catNms=CATEGORY_NAMES);
imgIds_train = coco_train.getImgIds(catIds=catIds_train);
imgDict_train = coco_train.loadImgs(imgIds_train)
len(imgIds_train) , len(catIds_train)
coco_val = coco.COCO(ANNOTATION_FILE_VAL)
catIds_val = coco_val.getCatIds(catNms=CATEGORY_NAMES);
imgIds_val = coco_val.getImgIds(catIds=catIds_val);
imgDict_val = coco_val.loadImgs(imgIds_val)
len(imgIds_val) , len(catIds_val)

loading annotations into memory...
Done (t=7.76s)
creating index...
index created!
loading annotations into memory...
Done (t=0.24s)
creating index...
index created!


(10, 4)

In [ ]:
from random import shuffle


shuffle(imgIds_train)
shuffle(imgIds_val)

imgIds_train = imgIds_train[0:6000]
imgIds_val = imgIds_val[0:600]

In [53]:
train_images_person = ["COCO_train2017_{0:012d}.jpg".format(ids) for ids in imgIds_train]
val_images_person = ["COCO_val2017_{0:012d}.jpg".format(ids) for ids in imgIds_val]

In [54]:
train_images_person

['COCO_train2017_000000562176.jpg',
 'COCO_train2017_000000344067.jpg',
 'COCO_train2017_000000203269.jpg',
 'COCO_train2017_000000340998.jpg',
 'COCO_train2017_000000226825.jpg',
 'COCO_train2017_000000262670.jpg',
 'COCO_train2017_000000465424.jpg',
 'COCO_train2017_000000057361.jpg',
 'COCO_train2017_000000012818.jpg',
 'COCO_train2017_000000078355.jpg',
 'COCO_train2017_000000294933.jpg',
 'COCO_train2017_000000298008.jpg',
 'COCO_train2017_000000242202.jpg',
 'COCO_train2017_000000267802.jpg',
 'COCO_train2017_000000575008.jpg',
 'COCO_train2017_000000283170.jpg',
 'COCO_train2017_000000210980.jpg',
 'COCO_train2017_000000301605.jpg',
 'COCO_train2017_000000053803.jpg',
 'COCO_train2017_000000564781.jpg',
 'COCO_train2017_000000506927.jpg',
 'COCO_train2017_000000551472.jpg',
 'COCO_train2017_000000246833.jpg',
 'COCO_train2017_000000014388.jpg',
 'COCO_train2017_000000225848.jpg',
 'COCO_train2017_000000455228.jpg',
 'COCO_train2017_000000372804.jpg',
 'COCO_train2017_00000012397

In [29]:
import glob
from os.path import exists
import os

In [68]:
"/".join(["A", "b"])

'A/b'

In [72]:
!ls

 1.jpg		  help.py		  runs
'1 net.ipynb'	  image.jpg		  sample.jpg
 2.jpg		  logs			  temp.png
 3.jpg		  mask_train_2017	  train.py
 4.jpg		  mask_val_2017		  unet_pytorch_notebook.ipynb
 annotations	  model.py		  Untitled1.ipynb
 car.jpg	  models		  Untitled.ipynb
 city-image.jpg   MY_NOTEBOOK.ipynb	  wget-log
 cocoapi	  predict.py		  wget-log.1
 content	  predict.pz		  wget-log.2
 firsttry.py	  __pycache__
 generator.py	  result_18.03.2022.jpg


In [52]:
filenames = glob.glob('../fiftyone/coco-2017/train/data/*')
list_file =  map(lambda x: x.rsplit("/", 1), filenames)

In [53]:
list_file

In [54]:
for file in map(lambda x: x.rsplit("/", 1), sorted(filenames)):
    print(f"mask_train_2017/COCO_train2017_{file[1]}", exists(f"mask_train_2017/COCO_train2017_{file[1]}"))
    

mask_train_2017/COCO_train2017_000000001315.jpg True
mask_train_2017/COCO_train2017_000000004376.jpg True
mask_train_2017/COCO_train2017_000000006233.jpg True
mask_train_2017/COCO_train2017_000000009801.jpg True
mask_train_2017/COCO_train2017_000000012818.jpg True
mask_train_2017/COCO_train2017_000000012946.jpg True
mask_train_2017/COCO_train2017_000000012993.jpg True
mask_train_2017/COCO_train2017_000000013230.jpg True
mask_train_2017/COCO_train2017_000000014388.jpg True
mask_train_2017/COCO_train2017_000000015451.jpg True
mask_train_2017/COCO_train2017_000000018214.jpg True
mask_train_2017/COCO_train2017_000000021711.jpg True
mask_train_2017/COCO_train2017_000000022741.jpg True
mask_train_2017/COCO_train2017_000000027975.jpg True
mask_train_2017/COCO_train2017_000000028855.jpg True
mask_train_2017/COCO_train2017_000000032458.jpg True
mask_train_2017/COCO_train2017_000000032471.jpg True
mask_train_2017/COCO_train2017_000000032533.jpg True
mask_train_2017/COCO_train2017_000000037209.jp

In [32]:
for file in map(lambda x: x.rsplit("/", 1), sorted(filenames)):
    if not exists(f"mask_train_2017/COCO_train2017_{file[1]}"):
        print(f"mask_train_2017/COCO_train2017_{file[1]}", exists(f"mask_train_2017/COCO_train2017_{file[1]}"))
        os.remove("/".join(file))

mask_train_2017/COCO_train2017_000000000036.jpg False
mask_train_2017/COCO_train2017_000000000049.jpg False
mask_train_2017/COCO_train2017_000000000061.jpg False
mask_train_2017/COCO_train2017_000000000064.jpg False
mask_train_2017/COCO_train2017_000000000071.jpg False
mask_train_2017/COCO_train2017_000000000073.jpg False
mask_train_2017/COCO_train2017_000000000074.jpg False
mask_train_2017/COCO_train2017_000000000077.jpg False
mask_train_2017/COCO_train2017_000000000086.jpg False
mask_train_2017/COCO_train2017_000000000094.jpg False
mask_train_2017/COCO_train2017_000000000109.jpg False
mask_train_2017/COCO_train2017_000000000110.jpg False
mask_train_2017/COCO_train2017_000000000113.jpg False
mask_train_2017/COCO_train2017_000000000127.jpg False
mask_train_2017/COCO_train2017_000000000136.jpg False
mask_train_2017/COCO_train2017_000000000149.jpg False
mask_train_2017/COCO_train2017_000000000151.jpg False
mask_train_2017/COCO_train2017_000000000165.jpg False
mask_train_2017/COCO_train20

mask_train_2017/COCO_train2017_000000010484.jpg False
mask_train_2017/COCO_train2017_000000010496.jpg False
mask_train_2017/COCO_train2017_000000010498.jpg False
mask_train_2017/COCO_train2017_000000010526.jpg False
mask_train_2017/COCO_train2017_000000010534.jpg False
mask_train_2017/COCO_train2017_000000010540.jpg False
mask_train_2017/COCO_train2017_000000010545.jpg False
mask_train_2017/COCO_train2017_000000010560.jpg False
mask_train_2017/COCO_train2017_000000010579.jpg False
mask_train_2017/COCO_train2017_000000010581.jpg False
mask_train_2017/COCO_train2017_000000010591.jpg False
mask_train_2017/COCO_train2017_000000010600.jpg False
mask_train_2017/COCO_train2017_000000010613.jpg False
mask_train_2017/COCO_train2017_000000010614.jpg False
mask_train_2017/COCO_train2017_000000010615.jpg False
mask_train_2017/COCO_train2017_000000010621.jpg False
mask_train_2017/COCO_train2017_000000010624.jpg False
mask_train_2017/COCO_train2017_000000010639.jpg False
mask_train_2017/COCO_train20

mask_train_2017/COCO_train2017_000000021284.jpg False
mask_train_2017/COCO_train2017_000000021285.jpg False
mask_train_2017/COCO_train2017_000000021292.jpg False
mask_train_2017/COCO_train2017_000000021310.jpg False
mask_train_2017/COCO_train2017_000000021329.jpg False
mask_train_2017/COCO_train2017_000000021330.jpg False
mask_train_2017/COCO_train2017_000000021343.jpg False
mask_train_2017/COCO_train2017_000000021365.jpg False
mask_train_2017/COCO_train2017_000000021378.jpg False
mask_train_2017/COCO_train2017_000000021383.jpg False
mask_train_2017/COCO_train2017_000000021394.jpg False
mask_train_2017/COCO_train2017_000000021400.jpg False
mask_train_2017/COCO_train2017_000000021404.jpg False
mask_train_2017/COCO_train2017_000000021417.jpg False
mask_train_2017/COCO_train2017_000000021419.jpg False
mask_train_2017/COCO_train2017_000000021423.jpg False
mask_train_2017/COCO_train2017_000000021452.jpg False
mask_train_2017/COCO_train2017_000000021459.jpg False
mask_train_2017/COCO_train20

mask_train_2017/COCO_train2017_000000037323.jpg False
mask_train_2017/COCO_train2017_000000037325.jpg False
mask_train_2017/COCO_train2017_000000037326.jpg False
mask_train_2017/COCO_train2017_000000037327.jpg False
mask_train_2017/COCO_train2017_000000037343.jpg False
mask_train_2017/COCO_train2017_000000037354.jpg False
mask_train_2017/COCO_train2017_000000037396.jpg False
mask_train_2017/COCO_train2017_000000037401.jpg False
mask_train_2017/COCO_train2017_000000037403.jpg False
mask_train_2017/COCO_train2017_000000037413.jpg False
mask_train_2017/COCO_train2017_000000037429.jpg False
mask_train_2017/COCO_train2017_000000037456.jpg False
mask_train_2017/COCO_train2017_000000037468.jpg False
mask_train_2017/COCO_train2017_000000037478.jpg False
mask_train_2017/COCO_train2017_000000037492.jpg False
mask_train_2017/COCO_train2017_000000037502.jpg False
mask_train_2017/COCO_train2017_000000037513.jpg False
mask_train_2017/COCO_train2017_000000037514.jpg False
mask_train_2017/COCO_train20

mask_train_2017/COCO_train2017_000000050980.jpg False
mask_train_2017/COCO_train2017_000000050988.jpg False
mask_train_2017/COCO_train2017_000000050992.jpg False
mask_train_2017/COCO_train2017_000000050995.jpg False
mask_train_2017/COCO_train2017_000000051025.jpg False
mask_train_2017/COCO_train2017_000000051040.jpg False
mask_train_2017/COCO_train2017_000000051045.jpg False
mask_train_2017/COCO_train2017_000000051046.jpg False
mask_train_2017/COCO_train2017_000000051052.jpg False
mask_train_2017/COCO_train2017_000000051054.jpg False
mask_train_2017/COCO_train2017_000000051067.jpg False
mask_train_2017/COCO_train2017_000000051070.jpg False
mask_train_2017/COCO_train2017_000000051079.jpg False
mask_train_2017/COCO_train2017_000000051083.jpg False
mask_train_2017/COCO_train2017_000000051089.jpg False
mask_train_2017/COCO_train2017_000000051100.jpg False
mask_train_2017/COCO_train2017_000000051110.jpg False
mask_train_2017/COCO_train2017_000000051119.jpg False
mask_train_2017/COCO_train20

...

mask_train_2017/COCO_train2017_000000512346.jpg False
mask_train_2017/COCO_train2017_000000512375.jpg False
mask_train_2017/COCO_train2017_000000512380.jpg False
mask_train_2017/COCO_train2017_000000512387.jpg False
mask_train_2017/COCO_train2017_000000512390.jpg False
mask_train_2017/COCO_train2017_000000512394.jpg False
mask_train_2017/COCO_train2017_000000512400.jpg False
mask_train_2017/COCO_train2017_000000512405.jpg False
mask_train_2017/COCO_train2017_000000512411.jpg False
mask_train_2017/COCO_train2017_000000512416.jpg False
mask_train_2017/COCO_train2017_000000512418.jpg False
mask_train_2017/COCO_train2017_000000512424.jpg False
mask_train_2017/COCO_train2017_000000512436.jpg False
mask_train_2017/COCO_train2017_000000512442.jpg False
mask_train_2017/COCO_train2017_000000512449.jpg False
mask_train_2017/COCO_train2017_000000512451.jpg False
mask_train_2017/COCO_train2017_000000512455.jpg False
mask_train_2017/COCO_train2017_000000512458.jpg False
mask_train_2017/COCO_train20

mask_train_2017/COCO_train2017_000000526800.jpg False
mask_train_2017/COCO_train2017_000000526810.jpg False
mask_train_2017/COCO_train2017_000000526825.jpg False
mask_train_2017/COCO_train2017_000000526837.jpg False
mask_train_2017/COCO_train2017_000000526840.jpg False
mask_train_2017/COCO_train2017_000000526856.jpg False
mask_train_2017/COCO_train2017_000000526861.jpg False
mask_train_2017/COCO_train2017_000000526867.jpg False
mask_train_2017/COCO_train2017_000000526874.jpg False
mask_train_2017/COCO_train2017_000000526877.jpg False
mask_train_2017/COCO_train2017_000000526881.jpg False
mask_train_2017/COCO_train2017_000000526887.jpg False
mask_train_2017/COCO_train2017_000000526892.jpg False
mask_train_2017/COCO_train2017_000000526904.jpg False
mask_train_2017/COCO_train2017_000000526912.jpg False
mask_train_2017/COCO_train2017_000000526922.jpg False
mask_train_2017/COCO_train2017_000000526933.jpg False
mask_train_2017/COCO_train2017_000000526940.jpg False
mask_train_2017/COCO_train20

mask_train_2017/COCO_train2017_000000541117.jpg False
mask_train_2017/COCO_train2017_000000541131.jpg False
mask_train_2017/COCO_train2017_000000541132.jpg False
mask_train_2017/COCO_train2017_000000541134.jpg False
mask_train_2017/COCO_train2017_000000541169.jpg False
mask_train_2017/COCO_train2017_000000541171.jpg False
mask_train_2017/COCO_train2017_000000541174.jpg False
mask_train_2017/COCO_train2017_000000541197.jpg False
mask_train_2017/COCO_train2017_000000541202.jpg False
mask_train_2017/COCO_train2017_000000541203.jpg False
mask_train_2017/COCO_train2017_000000541208.jpg False
mask_train_2017/COCO_train2017_000000541209.jpg False
mask_train_2017/COCO_train2017_000000541212.jpg False
mask_train_2017/COCO_train2017_000000541231.jpg False
mask_train_2017/COCO_train2017_000000541251.jpg False
mask_train_2017/COCO_train2017_000000541280.jpg False
mask_train_2017/COCO_train2017_000000541282.jpg False
mask_train_2017/COCO_train2017_000000541290.jpg False
mask_train_2017/COCO_train20

mask_train_2017/COCO_train2017_000000559484.jpg False
mask_train_2017/COCO_train2017_000000559511.jpg False
mask_train_2017/COCO_train2017_000000559522.jpg False
mask_train_2017/COCO_train2017_000000559525.jpg False
mask_train_2017/COCO_train2017_000000559550.jpg False
mask_train_2017/COCO_train2017_000000559553.jpg False
mask_train_2017/COCO_train2017_000000559557.jpg False
mask_train_2017/COCO_train2017_000000559566.jpg False
mask_train_2017/COCO_train2017_000000559586.jpg False
mask_train_2017/COCO_train2017_000000559619.jpg False
mask_train_2017/COCO_train2017_000000559633.jpg False
mask_train_2017/COCO_train2017_000000559645.jpg False
mask_train_2017/COCO_train2017_000000559647.jpg False
mask_train_2017/COCO_train2017_000000559652.jpg False
mask_train_2017/COCO_train2017_000000559656.jpg False
mask_train_2017/COCO_train2017_000000559665.jpg False
mask_train_2017/COCO_train2017_000000559685.jpg False
mask_train_2017/COCO_train2017_000000559720.jpg False
mask_train_2017/COCO_train20

mask_train_2017/COCO_train2017_000000576399.jpg False
mask_train_2017/COCO_train2017_000000576417.jpg False
mask_train_2017/COCO_train2017_000000576427.jpg False
mask_train_2017/COCO_train2017_000000576431.jpg False
mask_train_2017/COCO_train2017_000000576445.jpg False
mask_train_2017/COCO_train2017_000000576449.jpg False
mask_train_2017/COCO_train2017_000000576457.jpg False
mask_train_2017/COCO_train2017_000000576461.jpg False
mask_train_2017/COCO_train2017_000000576463.jpg False
mask_train_2017/COCO_train2017_000000576468.jpg False
mask_train_2017/COCO_train2017_000000576500.jpg False
mask_train_2017/COCO_train2017_000000576517.jpg False
mask_train_2017/COCO_train2017_000000576518.jpg False
mask_train_2017/COCO_train2017_000000576526.jpg False
mask_train_2017/COCO_train2017_000000576527.jpg False
mask_train_2017/COCO_train2017_000000576530.jpg False
mask_train_2017/COCO_train2017_000000576539.jpg False
mask_train_2017/COCO_train2017_000000576582.jpg False
mask_train_2017/COCO_train20

In [48]:
filenames = glob.glob('../fiftyone/coco-2017/validation/data/*')
list_file =  map(lambda x: x.rsplit("/", 1), filenames)


In [49]:
for file in map(lambda x: x.rsplit("/", 1), sorted(filenames)):
    if not exists(f"mask_val_2017/COCO_val2017_{file[1]}"):
        print(f"mask_val_2017/COCO_val2017_{file[1]}", exists(f"mask_val_2017/COCO_val2017_{file[1]}"))
        os.remove("/".join(file))

In [51]:
for file in map(lambda x: x.rsplit("/", 1), sorted(filenames)):
    print(f"mask_val_2017/COCO_val2017_{file[1]}", exists(f"mask_val_2017/COCO_val2017_{file[1]}"))


mask_val_2017/COCO_val2017_000000122166.jpg True
mask_val_2017/COCO_val2017_000000135410.jpg True
mask_val_2017/COCO_val2017_000000139099.jpg True
mask_val_2017/COCO_val2017_000000226417.jpg True
mask_val_2017/COCO_val2017_000000254814.jpg True
mask_val_2017/COCO_val2017_000000296649.jpg True
mask_val_2017/COCO_val2017_000000350023.jpg True
mask_val_2017/COCO_val2017_000000357737.jpg True
mask_val_2017/COCO_val2017_000000411938.jpg True
mask_val_2017/COCO_val2017_000000490936.jpg True
